Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [1]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
%cd ..

C:\Users\domstr2\l07


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  1 8714k    1 95352    0     0  66216      0  0:02:14  0:00:01  0:02:13 93666
100 8714k  100 8714k    0     0  4211k      0  0:00:02  0:00:02 --:--:-- 5290k


C:\Users\domstr2


'unzip' is not recognized as an internal or external command,
operable program or batch file.


Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [30]:
!pip3 install conllu
import codecs
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]

with open('l07/Janet_test.conllu', encoding='utf-8') as trainfile:
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open('l07/Janet_test.conllu', encoding='utf-8') as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))

Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [31]:
!pip3 install tabulate
from tabulate import tabulate
tabulate(trainset[0], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>hej</td><td>greeting</td><td>O</td></tr>\n</tbody>\n</table>'

In [32]:
tabulate(trainset[10], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chcialbym</td><td>prescription/collect</td><td>O</td></tr>\n<tr><td style="text-align: right;">2</td><td>odebrac  </td><td>prescription/collect</td><td>O</td></tr>\n<tr><td style="text-align: right;">3</td><td>receptę  </td><td>prescription/collect</td><td>O</td></tr>\n</tbody>\n</table>'

In [33]:
tabulate(trainset[1], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;"> 1</td><td>dzień          </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 2</td><td>dobry,         </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 3</td><td>chciałbym      </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 4</td><td>umówić         </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 5</td><td>się            </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 6</td><td>na             </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 7</td><td>wizytę         </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 8</td><td>do             </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;"> 9</td><td>lekarza        </td><td>appoinment/create_appointment</td><td>B-appoinment/doctor</td></tr>\n<tr><td style="text-align: right;">10</td><td>rodzinnego.    </td><td>appoinment/create_appointment</td><td>I-appoinment/doctor</td></tr>\n<tr><td style="text-align: right;">11</td><td>najlepiej      </td><td>appoinment/create_appointment</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">12</td><td>dzisiaj        </td><td>appoinment/create_appointment</td><td>B-datetime         </td></tr>\n<tr><td style="text-align: right;">13</td><td>w              </td><td>appoinment/create_appointment</td><td>I-datetime         </td></tr>\n<tr><td style="text-align: right;">14</td><td>godzinach      </td><td>appoinment/create_appointment</td><td>I-datetime         </td></tr>\n<tr><td style="text-align: right;">15</td><td>popołudniowych.</td><td>appoinment/create_appointment</td><td>I-datetime         </td></tr>\n</tbody>\n</table>'

Na potrzeby prezentacji procesu uczenia w jupyterowym notatniku zawęzimy zbiór danych do początkowych przykładów.

In [13]:
trainset = trainset[:100]
testset = testset[:100]

In [25]:
print('ąę')

ąę


Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [14]:
!pip3 install flair
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

!pip3 install torch
# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

  Using cached requests-2.25.1-py2.py3-none-any.whl (61 kB)
  Attempting uninstall: requests
    Found existing installation: requests 2.24.0
    Uninstalling requests-2.24.0:
      Successfully uninstalled requests-2.24.0


ERROR: After October 2020 you may experience errors when installing or updating packages. This is because pip will change the way that it resolves dependency conflicts.

We recommend you use --use-feature=2020-resolver to test your packages with the new resolver before it becomes the default.

conda 4.10.1 requires ruamel_yaml_conda>=0.11.14, which is not installed.


Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [34]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label:
                ftoken.add_tag(label, token[label])

            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Corpus: 37 train + 4 dev + 41 test sentences
Dictionary with 13 tags: <unk>, O, B-appoinment/doctor, I-appoinment/doctor, B-datetime, I-datetime, B-login/id, B-login/password, B-appointment/type, I-appointment/type, B-prescription/type, <START>, <STOP>


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [24]:
embedding_types = [
    WordEmbeddings('pl'),
    FlairEmbeddings('pl-forward'),
    FlairEmbeddings('pl-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

2021-05-12 17:01:27,807 https://flair.informatik.hu-berlin.de/resources/embeddings/token/pl-wiki-fasttext-300d-1M.vectors.npy not found in cache, downloading to C:\Users\domstr2\AppData\Local\Temp\tmpq9mlzfps


100%|██████████| 1199998928/1199998928 [00:52<00:00, 22832915.30B/s]

2021-05-12 17:02:20,552 copying C:\Users\domstr2\AppData\Local\Temp\tmpq9mlzfps to cache at C:\Users\domstr2\.flair\embeddings\pl-wiki-fasttext-300d-1M.vectors.npy


2021-05-12 17:02:32,864 removing temp file C:\Users\domstr2\AppData\Local\Temp\tmpq9mlzfps
2021-05-12 17:02:33,344 https://flair.informatik.hu-berlin.de/resources/embeddings/token/pl-wiki-fasttext-300d-1M not found in cache, downloading to C:\Users\domstr2\AppData\Local\Temp\tmpp2reld0s


100%|██████████| 40874795/40874795 [00:01<00:00, 21969279.66B/s]

...

2021-05-12 17:02:42,804 copying C:\Users\domstr2\AppData\Local\Temp\tmpin9zi6n_ to cache at C:\Users\domstr2\.flair\embeddings\lm-polish-forward-v0.2.pt


2021-05-12 17:02:42,861 removing temp file C:\Users\domstr2\AppData\Local\Temp\tmpin9zi6n_
2021-05-12 17:02:43,329 https://flair.informatik.hu-berlin.de/resources/embeddings/flair/lm-polish-backward-v0.2.pt not found in cache, downloading to C:\Users\domstr2\AppData\Local\Temp\tmp30skh32n


100%|██████████| 84244196/84244196 [00:03<00:00, 25790261.34B/s]

2021-05-12 17:02:46,769 copying C:\Users\domstr2\AppData\Local\Temp\tmp30skh32n to cache at C:\Users\domstr2\.flair\embeddings\lm-polish-backward-v0.2.pt


2021-05-12 17:02:46,828 removing temp file C:\Users\domstr2\AppData\Local\Temp\tmp30skh32n


Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [35]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectiona

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [36]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=10,
              train_with_dev=False)

2021-05-12 17:07:41,538 ----------------------------------------------------------------------------------------------------
2021-05-12 17:07:41,539 Model: "SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dr

RuntimeError: [enforce fail at ..\caffe2\serialize\inline_container.cc:274] . unexpected pos 64 vs 0

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [19]:
model = SequenceTagger.load('slot-model/final-model.pt')

2021-05-12 16:58:59,033 loading file slot-model/final-model.pt


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [20]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]


Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [23]:
tabulate(predict(model, 'doktor lekarz wizyta kolano na godzine jutro dzisiaj 13:00'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>doktor </td><td>O</td></tr>\n<tr><td>lekarz </td><td>O</td></tr>\n<tr><td>wizyta </td><td>O</td></tr>\n<tr><td>kolano </td><td>O</td></tr>\n<tr><td>na     </td><td>O</td></tr>\n<tr><td>godzine</td><td>O</td></tr>\n<tr><td>jutro  </td><td>O</td></tr>\n<tr><td>dzisiaj</td><td>O</td></tr>\n<tr><td>13:00  </td><td>O</td></tr>\n</tbody>\n</table>'

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
